In [4]:
%%capture
!pip install datasets --upgrade --user
!pip install transformers --upgrade --user
#!pip install torchaudio==0.10.0+cu113 -f https://download.pytorch.org/whl/cu113/torch_stable.html
!pip install librosa
!pip install jiwer
#!pip install kaggle
!pip install huggingface_hub==0.1

In [1]:
import transformers
transformers.__version__

'4.17.0.dev0'

In [2]:
import torchaudio
torchaudio.__version__

'0.10.2+cu102'

In [3]:
import datasets
from datasets import load_dataset, load_metric, Audio
datasets.set_caching_enabled(False)
print(datasets.__version__)

1.18.3


In [4]:
# Environment settings: 
import pandas as pd
pd.set_option('display.max_column', None)
pd.set_option('display.max_rows', None)
pd.set_option('display.max_seq_items', None)
pd.set_option('display.max_colwidth', 500)
pd.set_option('expand_frame_repr', True)

from datasets import concatenate_datasets, load_dataset, Audio

In [5]:
from huggingface_hub import notebook_login

notebook_login()

In [6]:
!git config --global credential.helper store

In [7]:
%%capture
!apt install git-lfs

In [8]:
common_voice_train = load_dataset("mozilla-foundation/common_voice_8_0", "et", split="train+validation+other", use_auth_token=True)

Downloading:   0%|          | 0.00/10.1k [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/2.98k [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/53.1k [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/1.12G [00:00<?, ?B/s]

0 examples [00:00, ? examples/s]

0 examples [00:00, ? examples/s]

0 examples [00:00, ? examples/s]

0 examples [00:00, ? examples/s]

0 examples [00:00, ? examples/s]

Dataset common_voice downloaded and prepared to /workspace/.cache/huggingface/datasets/mozilla-foundation___common_voice/et/8.0.0/b8bc4d453193c06a43269b46cd87f075c70f152ac963b7f28f7a2760c45ec3e8. Subsequent calls will reuse this data.


In [9]:
common_voice_test = load_dataset("mozilla-foundation/common_voice_8_0", "et", split="test", use_auth_token=True)

Reusing dataset common_voice (/workspace/.cache/huggingface/datasets/mozilla-foundation___common_voice/et/8.0.0/b8bc4d453193c06a43269b46cd87f075c70f152ac963b7f28f7a2760c45ec3e8)


In [10]:
common_voice_train[0]


{'client_id': 'fa7f67d93b2f3a6e685275897b5b67653df98a2880d1a8e4550274bb2420a4965e5561a92daf604000bedf67bd9958be1c8c8c1bd54322c265024890d56e51da',
 'path': 'cv-corpus-8.0-2022-01-19/et/clips/common_voice_et_18039906.mp3',
 'audio': {'path': 'cv-corpus-8.0-2022-01-19/et/clips/common_voice_et_18039906.mp3',
  'array': array([0.0000000e+00, 0.0000000e+00, 0.0000000e+00, ..., 4.0411949e-05,
         3.4034252e-05, 3.7550926e-05], dtype=float32),
  'sampling_rate': 48000},
 'sentence': 'Kusjuures selle nimel Mägi riskis isiklikult ja riskis suurelt.',
 'up_votes': 2,
 'down_votes': 0,
 'age': 'thirties',
 'gender': 'male',
 'accent': '',
 'locale': 'et',
 'segment': ''}

In [11]:
common_voice_test[0]

{'client_id': 'e570aa634f53f3496f29b20b54b7fc501e1b5b9e6d2cfc41ebbd090bbc3682555b25d632f5b7675b69a98a4da07ff084f6aa633c98051db90f2aaa36224af9e4',
 'path': 'cv-corpus-8.0-2022-01-19/et/clips/common_voice_et_18031888.mp3',
 'audio': {'path': 'cv-corpus-8.0-2022-01-19/et/clips/common_voice_et_18031888.mp3',
  'array': array([ 0.        ,  0.        ,  0.        , ..., -0.00384867,
         -0.00353348, -0.00356781], dtype=float32),
  'sampling_rate': 48000},
 'sentence': 'Aleksejevi sõnul on ka selle osa laevast disaininud Baltic Workboatsi insenerid.',
 'up_votes': 2,
 'down_votes': 0,
 'age': '',
 'gender': '',
 'accent': '',
 'locale': 'et',
 'segment': ''}

In [12]:
common_voice_train = common_voice_train.remove_columns(['client_id','up_votes', 'down_votes', 'age', 'gender', 'accent', 'locale', 'segment'])
common_voice_test = common_voice_test.remove_columns(['client_id','up_votes', 'down_votes', 'age', 'gender', 'accent', 'locale', 'segment'])

In [13]:
from datasets import ClassLabel
import random
import pandas as pd
from IPython.display import display, HTML

def show_random_elements(dataset, num_examples=10):
    assert num_examples <= len(dataset), "Can't pick more elements than there are in the dataset."
    picks = []
    for _ in range(num_examples):
        pick = random.randint(0, len(dataset)-1)
        while pick in picks:
            pick = random.randint(0, len(dataset)-1)
        picks.append(pick)
    
    df = pd.DataFrame(dataset[picks])
    display(HTML(df.to_html()))

In [14]:
show_random_elements(common_voice_train.remove_columns(["path", "audio"]), num_examples=10)

In [15]:
import re
CHARS_TO_IGNORE = [",", "?", "¿", ".", "!", "¡", ";", "；", ":", '""', "%", '"', "�", "ʿ", "·", "჻", "~", "՞",
                   "؟", "،", "।", "॥", "«", "»", "„", "“", "”", "「", "」", "‘", "’", "《", "》", "(", ")", "[", "]",
                   "{", "}", "=", "`", "_", "+", "<", ">", "…", "–", "°", "´", "ʾ", "‹", "›", "©", "®", "—", "→", "。",
                   "、", "﹂", "﹁", "‧", "～", "﹏", "，", "｛", "｝", "（", "）", "［", "］", "【", "】", "‥", "〽",
                   "『", "』", "〝", "〟", "⟨", "⟩", "〜", "：", "！", "？", "♪", "؛", "/", "\\", "º", "−", "^", "ʻ", "ˆ"]


chars_to_remove_regex = f"[{re.escape(''.join(CHARS_TO_IGNORE))}]"

def remove_special_characters(batch):
    batch["sentence"] = re.sub(chars_to_remove_regex, '', batch["sentence"]).lower()
    batch["sentence"] = re.sub('[-]', ' ', batch["sentence"]).lower()
    return batch

In [16]:
common_voice_train = common_voice_train.map(remove_special_characters)
common_voice_test = common_voice_test.map(remove_special_characters)

0ex [00:00, ?ex/s]

0ex [00:00, ?ex/s]

In [17]:
def extract_all_chars(batch):
  all_text = " ".join(batch["sentence"])
  vocab = list(set(all_text))
  return {"vocab": [vocab], "all_text": [all_text]}

In [18]:
vocab_train = common_voice_train.map(extract_all_chars, batched=True, batch_size=-1, keep_in_memory=True, remove_columns=common_voice_train.column_names)
vocab_test = common_voice_test.map(extract_all_chars, batched=True, batch_size=-1, keep_in_memory=True, remove_columns=common_voice_test.column_names)

  0%|          | 0/1 [00:00<?, ?ba/s]

  0%|          | 0/1 [00:00<?, ?ba/s]

In [19]:
vocab_list = list(set(vocab_train["vocab"][0]) | set(vocab_test["vocab"][0]))

In [20]:
print(len(common_voice_train))
print(len(common_voice_test))

6521
2613


In [21]:
len(vocab_list)

35

In [22]:
vocab_list

['p',
 'ž',
 'y',
 'x',
 'e',
 'j',
 'a',
 'r',
 'ü',
 'n',
 'o',
 'g',
 ' ',
 'c',
 'i',
 'ö',
 '̇',
 'd',
 'm',
 's',
 't',
 'š',
 'f',
 'b',
 'h',
 'w',
 'k',
 'ä',
 'l',
 'v',
 "'",
 'q',
 'u',
 'z',
 'õ']

In [23]:
vocab_dict = {v: k for k, v in enumerate(sorted(vocab_list))}

In [24]:
vocab_dict["|"] = vocab_dict[" "]
del vocab_dict[" "]

In [25]:
vocab_dict

{"'": 1,
 'a': 2,
 'b': 3,
 'c': 4,
 'd': 5,
 'e': 6,
 'f': 7,
 'g': 8,
 'h': 9,
 'i': 10,
 'j': 11,
 'k': 12,
 'l': 13,
 'm': 14,
 'n': 15,
 'o': 16,
 'p': 17,
 'q': 18,
 'r': 19,
 's': 20,
 't': 21,
 'u': 22,
 'v': 23,
 'w': 24,
 'x': 25,
 'y': 26,
 'z': 27,
 'ä': 28,
 'õ': 29,
 'ö': 30,
 'ü': 31,
 'š': 32,
 'ž': 33,
 '̇': 34,
 '|': 0}

In [26]:
vocab_dict["[UNK]"] = len(vocab_dict)
vocab_dict["[PAD]"] = len(vocab_dict)
len(vocab_dict)

37

In [27]:
import json
with open('vocab.json', 'w') as vocab_file:
    json.dump(vocab_dict, vocab_file)

In [28]:
from transformers import Wav2Vec2CTCTokenizer

tokenizer = Wav2Vec2CTCTokenizer.from_pretrained("./", unk_token="[UNK]", pad_token="[PAD]", word_delimiter_token="|")

file ./config.json not found
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [29]:
repo_name = "wav2vec2-xlsr-1b-et"

In [30]:
tokenizer.push_to_hub(repo_name)

/opt/conda/lib/python3.8/site-packages/huggingface_hub/hf_api.py:1001: FutureWarning: `create_repo` now takes `token` as an optional positional argument. Be sure to adapt your code!
  warnings.warn(
Cloning https://huggingface.co/RASMUS/wav2vec2-xlsr-1b-et into local empty directory.
To https://huggingface.co/RASMUS/wav2vec2-xlsr-1b-et
   ecf61eb..69fdc69  main -> main



'https://huggingface.co/RASMUS/wav2vec2-xlsr-1b-et/commit/69fdc6958a35d1f5d8af7690b6a219722f1278d5'

In [31]:
from transformers import Wav2Vec2FeatureExtractor

feature_extractor = Wav2Vec2FeatureExtractor(feature_size=1, sampling_rate=16000, padding_value=0.0, do_normalize=True, return_attention_mask=True)

In [32]:
from transformers import Wav2Vec2Processor

processor = Wav2Vec2Processor(feature_extractor=feature_extractor, tokenizer=tokenizer)

In [33]:
import torchaudio

In [34]:
common_voice_train = common_voice_train.cast_column("audio", Audio(sampling_rate=16_000))
common_voice_test = common_voice_test.cast_column("audio", Audio(sampling_rate=16_000))

In [35]:
common_voice_train[0]["audio"]

{'path': 'cv-corpus-8.0-2022-01-19/et/clips/common_voice_et_18039906.mp3',
 'array': array([0.0000000e+00, 0.0000000e+00, 0.0000000e+00, ..., 2.8755874e-05,
        7.3133713e-05, 4.6529221e-05], dtype=float32),
 'sampling_rate': 16000}

In [36]:
def prepare_dataset(batch):
    audio = batch["audio"]

    # batched output is "un-batched"
    batch["input_values"] = processor(audio["array"], sampling_rate=audio["sampling_rate"]).input_values[0]
    batch["input_length"] = len(batch["input_values"])
    
    with processor.as_target_processor():
        batch["labels"] = processor(batch["sentence"]).input_ids
    return batch

In [37]:
common_voice_train = common_voice_train.map(prepare_dataset, remove_columns=common_voice_train.column_names)
print("done train")
common_voice_test = common_voice_test.map(prepare_dataset, remove_columns=common_voice_test.column_names)

0ex [00:00, ?ex/s]

done train


0ex [00:00, ?ex/s]

In [38]:
max_input_length = 20.0 * feature_extractor.sampling_rate
min_input_length = 0.0 * feature_extractor.sampling_rate

In [39]:
def is_audio_in_length_range(length):
    return length > min_input_length and length < max_input_length

In [40]:
common_voice_train = common_voice_train.filter(
            is_audio_in_length_range,
            input_columns=["input_length"],
        )

  0%|          | 0/7 [00:00<?, ?ba/s]

In [41]:
import torch

from dataclasses import dataclass, field
from typing import Any, Dict, List, Optional, Union
from transformers import AutoProcessor


@dataclass
class DataCollatorCTCWithPadding:
    """
    Data collator that will dynamically pad the inputs received.
    Args:
        processor (:class:`~transformers.AutoProcessor`)
            The processor used for proccessing the data.
        padding (:obj:`bool`, :obj:`str` or :class:`~transformers.tokenization_utils_base.PaddingStrategy`, `optional`, defaults to :obj:`True`):
            Select a strategy to pad the returned sequences (according to the model's padding side and padding index)
            among:
            * :obj:`True` or :obj:`'longest'`: Pad to the longest sequence in the batch (or no padding if only a single
              sequence if provided).
            * :obj:`'max_length'`: Pad to a maximum length specified with the argument :obj:`max_length` or to the
              maximum acceptable input length for the model if that argument is not provided.
            * :obj:`False` or :obj:`'do_not_pad'` (default): No padding (i.e., can output a batch with sequences of
              different lengths).
        max_length (:obj:`int`, `optional`):
            Maximum length of the ``input_values`` of the returned list and optionally padding length (see above).
        max_length_labels (:obj:`int`, `optional`):
            Maximum length of the ``labels`` returned list and optionally padding length (see above).
        pad_to_multiple_of (:obj:`int`, `optional`):
            If set will pad the sequence to a multiple of the provided value.
            This is especially useful to enable the use of Tensor Cores on NVIDIA hardware with compute capability >=
            7.5 (Volta).
    """

    processor: AutoProcessor
    padding: Union[bool, str] = "longest"
    pad_to_multiple_of: Optional[int] = None
    pad_to_multiple_of_labels: Optional[int] = None

    def __call__(self, features: List[Dict[str, Union[List[int], torch.Tensor]]]) -> Dict[str, torch.Tensor]:
        # split inputs and labels since they have to be of different lenghts and need
        # different padding methods
        input_features = [{"input_values": feature["input_values"]} for feature in features]
        label_features = [{"input_ids": feature["labels"]} for feature in features]

        batch = self.processor.pad(
            input_features,
            padding=self.padding,
            pad_to_multiple_of=self.pad_to_multiple_of,
            return_tensors="pt",
        )

        with self.processor.as_target_processor():
            labels_batch = self.processor.pad(
                label_features,
                padding=self.padding,
                pad_to_multiple_of=self.pad_to_multiple_of_labels,
                return_tensors="pt",
            )

        # replace padding with -100 to ignore loss correctly
        labels = labels_batch["input_ids"].masked_fill(labels_batch.attention_mask.ne(1), -100)

        batch["labels"] = labels

        return batch

In [42]:
data_collator = DataCollatorCTCWithPadding(processor=processor, padding=True)

In [43]:
wer_metric = load_metric("wer")

Downloading:   0%|          | 0.00/1.90k [00:00<?, ?B/s]

In [44]:
def compute_metrics(pred):
    pred_logits = pred.predictions
    pred_ids = np.argmax(pred_logits, axis=-1)

    pred.label_ids[pred.label_ids == -100] = processor.tokenizer.pad_token_id

    pred_str = processor.batch_decode(pred_ids)
    # we do not want to group tokens when computing the metrics
    label_str = processor.batch_decode(pred.label_ids, group_tokens=False)

    wer = wer_metric.compute(predictions=pred_str, references=label_str)

    return {"wer": wer}

In [45]:
from transformers import Wav2Vec2ForCTC

model = Wav2Vec2ForCTC.from_pretrained(
    "facebook/wav2vec2-xls-r-1b", 
    attention_dropout=0.094,
    hidden_dropout=0.047,
    feat_proj_dropout=0.04,
    mask_time_prob=0.082,
    layerdrop=0.041,
    activation_dropout=0.055,
    ctc_loss_reduction="mean", 
    pad_token_id=processor.tokenizer.pad_token_id,
    vocab_size=len(processor.tokenizer),
)
model.to('cuda')

Downloading:   0%|          | 0.00/1.53k [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/3.60G [00:00<?, ?B/s]

Some weights of the model checkpoint at facebook/wav2vec2-xls-r-1b were not used when initializing Wav2Vec2ForCTC: ['project_hid.weight', 'project_q.weight', 'quantizer.weight_proj.bias', 'quantizer.codevectors', 'quantizer.weight_proj.weight', 'project_q.bias', 'project_hid.bias']
- This IS expected if you are initializing Wav2Vec2ForCTC from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing Wav2Vec2ForCTC from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of Wav2Vec2ForCTC were not initialized from the model checkpoint at facebook/wav2vec2-xls-r-1b and are newly initialized: ['lm_head.bias', 'lm_head.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for 

Wav2Vec2ForCTC(
  (wav2vec2): Wav2Vec2Model(
    (feature_extractor): Wav2Vec2FeatureEncoder(
      (conv_layers): ModuleList(
        (0): Wav2Vec2LayerNormConvLayer(
          (conv): Conv1d(1, 512, kernel_size=(10,), stride=(5,))
          (layer_norm): LayerNorm((512,), eps=1e-05, elementwise_affine=True)
        )
        (1): Wav2Vec2LayerNormConvLayer(
          (conv): Conv1d(512, 512, kernel_size=(3,), stride=(2,))
          (layer_norm): LayerNorm((512,), eps=1e-05, elementwise_affine=True)
        )
        (2): Wav2Vec2LayerNormConvLayer(
          (conv): Conv1d(512, 512, kernel_size=(3,), stride=(2,))
          (layer_norm): LayerNorm((512,), eps=1e-05, elementwise_affine=True)
        )
        (3): Wav2Vec2LayerNormConvLayer(
          (conv): Conv1d(512, 512, kernel_size=(3,), stride=(2,))
          (layer_norm): LayerNorm((512,), eps=1e-05, elementwise_affine=True)
        )
        (4): Wav2Vec2LayerNormConvLayer(
          (conv): Conv1d(512, 512, kernel_size=(3,), 

In [47]:
model.freeze_feature_extractor()

In [48]:
import os
os.environ["WANDB_DISABLED"] = "true"

In [50]:
from transformers import TrainingArguments

training_args = TrainingArguments(
  output_dir=repo_name,
  group_by_length=True,
  per_device_train_batch_size=32,
  gradient_accumulation_steps=1,
  evaluation_strategy="steps",
  num_train_epochs=10,
  gradient_checkpointing=True,
  fp16=True,
  save_steps=500,
  eval_steps=500,
  logging_steps=50,
  learning_rate=5e-5,
  warmup_steps=500,
  save_total_limit=3,
  push_to_hub=True,
  load_best_model_at_end=True,
  greater_is_better=False,
  report_to="tensorboard",
  metric_for_best_model='eval_wer',
)

In [50]:
!nvidia-smi

Sat Feb  5 08:58:36 2022       
+-----------------------------------------------------------------------------+
| NVIDIA-SMI 460.32.03    Driver Version: 460.32.03    CUDA Version: 11.2     |
|-------------------------------+----------------------+----------------------+
| GPU  Name        Persistence-M| Bus-Id        Disp.A | Volatile Uncorr. ECC |
| Fan  Temp  Perf  Pwr:Usage/Cap|         Memory-Usage | GPU-Util  Compute M. |
|                               |                      |               MIG M. |
|===============================+======================+======================|
|   0  Tesla K80           Off  | 00000000:00:04.0 Off |                    0 |
| N/A   73C    P0    72W / 149W |   1806MiB / 11441MiB |      0%      Default |
|                               |                      |                  N/A |
+-------------------------------+----------------------+----------------------+
                                                                               
+-------

In [49]:
!pip install bitsandbytes-cuda111 --user

     |████████████████████████████████| 4.0 MB 24.2 MB/s            
You should consider upgrading via the '/opt/conda/bin/python -m pip install --upgrade pip' command.


In [52]:
!pip install tensorboard --user

     |████████████████████████████████| 5.8 MB 4.8 MB/s            
     |████████████████████████████████| 126 kB 99.3 MB/s            
     |████████████████████████████████| 156 kB 92.1 MB/s            
     |████████████████████████████████| 288 kB 80.4 MB/s            
     |████████████████████████████████| 97 kB 27.2 MB/s            
     |████████████████████████████████| 781 kB 97.0 MB/s            
     |████████████████████████████████| 4.1 MB 76.3 MB/s            
     |████████████████████████████████| 1.1 MB 76.3 MB/s            
     |████████████████████████████████| 4.9 MB 39.7 MB/s            
     |████████████████████████████████| 155 kB 99.3 MB/s            
     |████████████████████████████████| 77 kB 26.5 MB/s            
     |████████████████████████████████| 151 kB 104.7 MB/s            
  Consider adding this directory to PATH or, if you prefer to suppress this warning, use --no-warn-script-location.
  Consider adding this directory to PATH or, if you prefer

In [53]:
import bitsandbytes as bnb
from transformers import Trainer
from transformers.trainer_pt_utils import get_parameter_names

decay_parameters = get_parameter_names(model, [torch.nn.LayerNorm])
decay_parameters = [name for name in decay_parameters if "bias" not in name]
optimizer_grouped_parameters = [
    {
        "params": [p for n, p in model.named_parameters() if n in decay_parameters],
        "weight_decay": training_args.weight_decay,
    },
    {
        "params": [p for n, p in model.named_parameters() if n not in decay_parameters],
        "weight_decay": 0.0,
    },
]
optimizer = bnb.optim.Adam8bit(
    params=optimizer_grouped_parameters,
    lr=training_args.learning_rate,
    betas=(training_args.adam_beta1, training_args.adam_beta2),
    eps=training_args.adam_epsilon,
)

optimizers = (optimizer, None)

# Initialize Trainer
trainer = Trainer(
    model=model,
    data_collator=data_collator,
    args=training_args,
    compute_metrics=compute_metrics,
    train_dataset=common_voice_train,
    eval_dataset=common_voice_test,
    tokenizer=processor.feature_extractor,
    optimizers=optimizers,
)

/workspace/wav2vec2-xlsr-1b-et is already a clone of https://huggingface.co/RASMUS/wav2vec2-xlsr-1b-et. Make sure you pull the latest changes with `repo.git_pull()`.
Using amp half precision backend


In [54]:
import numpy as np

In [55]:
trainer.train()

The following columns in the training set  don't have a corresponding argument in `Wav2Vec2ForCTC.forward` and have been ignored: input_length.
***** Running training *****
  Num examples = 6521
  Num Epochs = 10
  Instantaneous batch size per device = 32
  Total train batch size (w. parallel, distributed & accumulation) = 32
  Gradient Accumulation steps = 1
  Total optimization steps = 2040


The following columns in the evaluation set  don't have a corresponding argument in `Wav2Vec2ForCTC.forward` and have been ignored: input_length.
***** Running Evaluation *****
  Num examples = 2613
  Batch size = 8
Saving model checkpoint to wav2vec2-xlsr-1b-et/checkpoint-500
Configuration saved in wav2vec2-xlsr-1b-et/checkpoint-500/config.json
Model weights saved in wav2vec2-xlsr-1b-et/checkpoint-500/pytorch_model.bin
Configuration saved in wav2vec2-xlsr-1b-et/checkpoint-500/preprocessor_config.json
Configuration saved in wav2vec2-xlsr-1b-et/preprocessor_config.json
The following columns in the evaluation set  don't have a corresponding argument in `Wav2Vec2ForCTC.forward` and have been ignored: input_length.
***** Running Evaluation *****
  Num examples = 2613
  Batch size = 8
Saving model checkpoint to wav2vec2-xlsr-1b-et/checkpoint-1000
Configuration saved in wav2vec2-xlsr-1b-et/checkpoint-1000/config.json
Model weights saved in wav2vec2-xlsr-1b-et/checkpoint-1000/pytorch_model.bi

TrainOutput(global_step=2040, training_loss=0.7346986307817347, metrics={'train_runtime': 10075.7398, 'train_samples_per_second': 6.472, 'train_steps_per_second': 0.202, 'total_flos': 4.170633739317263e+19, 'train_loss': 0.7346986307817347, 'epoch': 10.0})